In [82]:
import json
import re
import pandas as pd
from collections import defaultdict


def process_log_file(file_path: str) -> pd.DataFrame:
    """
    Efficiently parse and process the log file, filtering out negative numbers in activity metrics.
    """
    log_data = []
    timestamp_pattern = r"\[(.*?)\]"  # Match timestamp in square brackets

    with open(file_path, "r") as file:
        for line in file:
            match = re.match(timestamp_pattern, line)
            if not match:
                continue  # Skip lines without timestamps
            timestamp = match.group(1)
            json_data = line[match.end():].strip()  # Extract JSON part
            try:
                parsed_data = json.loads(json_data)
                if "roster" in parsed_data:
                    roster_data = parsed_data["roster"]
                    for roster_key, roster_value in roster_data.items():
                        player_data = json.loads(roster_value)
                        player_data["timestamp"] = timestamp
                        player_data["roster_key"] = roster_key

                        # Filter negative values
                        for key in ["kills", "deaths", "damage", "healed", "mitigated"]:
                            if key in player_data and isinstance(player_data[key], (int, float)) and player_data[key] < 0:
                                player_data[key] = 0

                        log_data.append(player_data)
            except json.JSONDecodeError:
                continue  # Ignore invalid JSON

    return pd.DataFrame(log_data)


def normalize_time(df: pd.DataFrame) -> pd.DataFrame:
    """
    Normalize timestamps for missing player data, efficiently using vectorized operations.
    """
    df["timestamp"] = pd.to_datetime(df["timestamp"])
    df = df.sort_values(by=["timestamp", "roster_key"])

    # Create a complete timestamp-player grid
    timestamps = df["timestamp"].unique()
    players = df["roster_key"].unique()
    grid = pd.MultiIndex.from_product([timestamps, players], names=["timestamp", "roster_key"])

    # Reindex DataFrame to fill in missing data
    df = df.set_index(["timestamp", "roster_key"]).reindex(grid).reset_index()

    # # Forward-fill player data across timestamps
    # df = df.sort_values(by=["roster_key", "timestamp"]).ffill()

    df = df.fillna(0)
    return df


# Example usage
file_path = "data/infoLog.txt"
df = process_log_file(file_path)
normalized_df = normalize_time(df)

# Save to CSV or analyze
normalized_df.to_csv("processed_log.csv", index=False, encoding="utf-8")
print(normalized_df)


                             timestamp roster_key player_name is_local  \
0     2024-11-28 19:08:54.152000+00:00   roster_6        SUKI    False   
1     2024-11-28 19:08:54.152000+00:00   roster_5           0        0   
2     2024-11-28 19:08:54.152000+00:00   roster_1           0        0   
3     2024-11-28 19:08:54.152000+00:00   roster_7           0        0   
4     2024-11-28 19:08:54.152000+00:00   roster_3           0        0   
...                                ...        ...         ...      ...   
87795 2024-11-28 20:54:01.775000+00:00   roster_9           0        0   
87796 2024-11-28 20:54:01.775000+00:00   roster_4           0        0   
87797 2024-11-28 20:54:01.775000+00:00   roster_0           0        0   
87798 2024-11-28 20:54:01.775000+00:00   roster_2           0        0   
87799 2024-11-28 20:54:01.775000+00:00   roster_8           0        0   

      hero_name hero_role  team  kills  deaths  damage  assists  healed  \
0       UNKNOWN   UNKNOWN   0.0    0

In [83]:
import pandas as pd

def cluster_fights(df: pd.DataFrame, time_threshold: int = 10) -> pd.DataFrame:
    """
    Cluster fight events based on activity and time gaps.

    Parameters:
    - df: DataFrame with normalized player data.
    - time_threshold: Maximum time (in seconds) between events in the same fight.

    Returns:
    - A DataFrame with fight clusters.
    """
    # Convert timestamp to datetime and sort
    df["timestamp"] = pd.to_datetime(df["timestamp"])
    df = df.sort_values("timestamp")

    # Aggregate metrics across all players for each timestamp
    aggregated = df.groupby("timestamp").agg(
        total_kills=("kills", "sum"),
        total_damage=("damage", "sum"),
        total_deaths=("deaths", "sum")
    ).reset_index()

    # Identify active periods (non-zero activity)
    aggregated["is_active"] = (
        (aggregated["total_kills"] > 0) |
        (aggregated["total_damage"] > 0) |
        (aggregated["total_deaths"] > 0)
    )

    # Calculate time gaps between consecutive active periods
    aggregated["time_diff"] = aggregated["timestamp"].diff().dt.total_seconds().fillna(0)
    aggregated["new_fight"] = (aggregated["time_diff"] > time_threshold)

    # Assign fight cluster IDs
    aggregated["fight_id"] = aggregated["new_fight"].cumsum()

    # Merge fight IDs back into the original data
    df = df.merge(aggregated[["timestamp", "fight_id", "is_active"]], on="timestamp")

    # Filter for active periods only
    fights = df[df["is_active"]].drop(columns=["is_active"])
    
    return fights

# Example usage
fights = cluster_fights(df)
print(fights)


       player_name  is_local hero_name hero_role  team  kills  deaths  \
4          ARYANNE     False  ZENYATTA   SUPPORT     1    0.0     0.0   
6          ARYANNE     False  ZENYATTA   SUPPORT     1    0.0     0.0   
7         MAISBÃ¤R      True       MEI    DAMAGE     1    0.0     0.0   
9        BIGBOYRUX     False  BAPTISTE   SUPPORT     0    0.0     0.0   
10    PHILIPHALLUS     False   ROADHOG      TANK     1    0.0     0.0   
...            ...       ...       ...       ...   ...    ...     ...   
8775           JOE     False      JUNO   SUPPORT     0   26.0     4.0   
8776           RAZ     False    SOMBRA    DAMAGE     1   13.0    13.0   
8777      PARZIVAL     False  DOOMFIST      TANK     0   35.0     6.0   
8778           JOE     False      JUNO   SUPPORT     0   26.0     4.0   
8779           JOE     False      JUNO   SUPPORT     0   26.0     4.0   

        damage  assists    healed  mitigated      battlenet_tag  is_teammate  \
4        43.00      0.0     0.000       0.0

In [84]:
def calculate_deltas(df: pd.DataFrame) -> pd.DataFrame:
    """
    Calculate deltas for cumulative metrics and filter negative values.

    Parameters:
    - df: DataFrame with normalized player data.

    Returns:
    - DataFrame with additional delta columns.
    """
    # Sort by timestamp and player
    df = df.sort_values(by=["roster_key", "timestamp"])

    # Calculate deltas for each player
    for col in ["kills", "deaths", "damage", "healed", "mitigated"]:
        df[f"{col}_delta"] = df.groupby("roster_key")[col].diff().fillna(0)
        # Ensure no negative deltas
        df[f"{col}_delta"] = df[f"{col}_delta"].clip(lower=0)

    return df



def cluster_fights_with_deltas(df: pd.DataFrame, time_threshold: int = 10) -> pd.DataFrame:
    """
    Cluster fight events based on deltas and time gaps.

    Parameters:
    - df: DataFrame with deltas calculated for cumulative metrics.
    - time_threshold: Maximum time (in seconds) between events in the same fight.

    Returns:
    - A DataFrame with fight clusters.
    """
    # Aggregate deltas across all players for each timestamp
    aggregated = df.groupby("timestamp").agg(
        total_kills_delta=("kills_delta", "sum"),
        total_damage_delta=("damage_delta", "sum"),
        total_healed_delta=("healed_delta", "sum"),
        total_deaths_delta=("deaths_delta", "sum"),
    ).reset_index()

    # Identify active periods (non-zero activity)
    aggregated["is_active"] = (
        (aggregated["total_kills_delta"] > 0) |
        (aggregated["total_damage_delta"] > 0) |
        (aggregated["total_healed_delta"] > 0) |
        (aggregated["total_deaths_delta"] > 0)
    )

    # Calculate time gaps between consecutive active periods
    aggregated["timestamp"] = pd.to_datetime(aggregated["timestamp"])
    aggregated = aggregated.sort_values("timestamp")
    aggregated["time_diff"] = aggregated["timestamp"].diff().dt.total_seconds().fillna(0)
    aggregated["new_fight"] = (aggregated["time_diff"] > time_threshold)

    # Assign fight cluster IDs
    aggregated["fight_id"] = aggregated["new_fight"].cumsum()

    # Merge fight IDs back into the original data
    df = df.merge(aggregated[["timestamp", "fight_id", "is_active"]], on="timestamp")

    # Filter for active periods only
    fights = df[df["is_active"]].drop(columns=["is_active"])

    return fights


# Example usage
df = calculate_deltas(df)  # Calculate deltas for cumulative metrics
fights = cluster_fights_with_deltas(df)  # Cluster fights using deltas

# Save or analyze the fight clusters
fights.to_csv("fight_clusters.csv", index=False)
print(fights)


     player_name  is_local hero_name hero_role  team  kills  deaths    damage  \
1      BIGBOYRUX     False  BAPTISTE   SUPPORT     0    0.0     0.0     62.50   
2      BIGBOYRUX     False  BAPTISTE   SUPPORT     0    0.0     0.0     62.50   
3      BIGBOYRUX     False  BAPTISTE   SUPPORT     0    0.0     0.0     62.50   
4      BIGBOYRUX     False  BAPTISTE   SUPPORT     0    0.0     0.0     62.50   
5      BIGBOYRUX     False  BAPTISTE   SUPPORT     0    0.0     0.0     62.50   
...          ...       ...       ...       ...   ...    ...     ...       ...   
8775    MAISBÃ¤R      True  DOOMFIST      TANK     1   16.0     8.0   9542.05   
8776    MAISBÃ¤R      True  DOOMFIST      TANK     1   16.0     8.0   9544.46   
8777    MAISBÃ¤R      True  DOOMFIST      TANK     1   16.0     8.0   9785.62   
8778    MAISBÃ¤R      True  DOOMFIST      TANK     1   16.0     8.0   9843.12   
8779    MAISBÃ¤R      True  DOOMFIST      TANK     1   17.0     8.0  10069.70   

      assists    healed  ..

In [85]:
def aggregate_fight_data(df: pd.DataFrame, damage_threshold=500, kills_threshold=1) -> pd.DataFrame:
    """
    Aggregate deltas across all players per timestamp and apply thresholds for fight detection.

    Parameters:
    - df: DataFrame with deltas calculated for cumulative metrics.
    - damage_threshold: Minimum total damage to consider a timestamp part of a fight.
    - kills_threshold: Minimum total kills to consider a timestamp part of a fight.

    Returns:
    - A DataFrame with aggregated metrics per timestamp and refined fight detection.
    """
    # Aggregate deltas for each timestamp
    aggregated = df.groupby("timestamp").agg(
        total_kills_delta=("kills_delta", "sum"),
        total_damage_delta=("damage_delta", "sum"),
        total_healed_delta=("healed_delta", "sum"),
        total_deaths_delta=("deaths_delta", "sum")
    ).reset_index()

    # Apply thresholds to detect fights
    aggregated["is_fight"] = (
        (aggregated["total_damage_delta"] >= damage_threshold) |
        (aggregated["total_kills_delta"] >= kills_threshold)
    )

    return aggregated


# Example usage
# df = process_log_file("example.log")  # Parse and normalize data
df = calculate_deltas(df)  # Calculate deltas for cumulative metrics
aggregated_fight_data = aggregate_fight_data(df)  # Aggregate fight data

# Save aggregated data
aggregated_fight_data.to_csv("aggregated_fight_data.csv", index=False)
print(aggregated_fight_data)


                            timestamp  total_kills_delta  total_damage_delta  \
0    2024-11-28 19:08:54.152000+00:00                0.0                0.00   
1    2024-11-28 19:09:01.175000+00:00                0.0                0.00   
2    2024-11-28 19:10:40.136000+00:00                0.0                0.00   
3    2024-11-28 19:11:37.715000+00:00                0.0                0.00   
4    2024-11-28 19:16:07.813000+00:00                0.0                0.00   
...                               ...                ...                 ...   
8775 2024-11-28 20:53:59.571000+00:00                2.0              273.32   
8776 2024-11-28 20:54:00.390000+00:00                1.0               89.65   
8777 2024-11-28 20:54:00.975000+00:00                2.0              151.48   
8778 2024-11-28 20:54:01.333000+00:00                0.0                0.00   
8779 2024-11-28 20:54:01.775000+00:00                0.0                0.00   

      total_healed_delta  total_deaths_

In [86]:
import plotly.graph_objects as go
import pandas as pd

def plot_activity_plotly(aggregated: pd.DataFrame):
    """
    Plot activity metrics over time to visualize fights using Plotly.

    Parameters:
    - aggregated: DataFrame with aggregated metrics (e.g., total_damage_delta, total_kills_delta).
    """
    # Convert timestamp to datetime if not already
    aggregated["timestamp"] = pd.to_datetime(aggregated["timestamp"])

    # Create a Plotly figure
    fig = go.Figure()

    # Add total damage to the primary y-axis
    fig.add_trace(
        go.Scatter(
            x=aggregated["timestamp"],
            y=aggregated["total_damage_delta"],
            mode="lines",
            name="Total Damage",
            line=dict(width=2, color="blue"),
        )
    )

    # Add total healing to the primary y-axis
    fig.add_trace(
        go.Scatter(
            x=aggregated["timestamp"],
            y=aggregated["total_healed_delta"],
            mode="lines",
            name="Total Healing",
            line=dict(width=2, color="green"),
        )
    )

    # Add total kills to the secondary y-axis
    fig.add_trace(
        go.Scatter(
            x=aggregated["timestamp"],
            y=aggregated["total_kills_delta"],
            mode="lines",
            name="Total Kills",
            line=dict(width=2, color="red"),
            yaxis="y2",
        )
    )

    # Highlight fight periods with markers
    fight_timestamps = aggregated[aggregated["is_fight"]]["timestamp"]
    fig.add_trace(
        go.Scatter(
            x=fight_timestamps,
            y=[0] * len(fight_timestamps),
            mode="markers",
            name="Fight Periods",
            marker=dict(size=10, color="orange", symbol="circle"),
        )
    )

    # Update layout with dual y-axes
    fig.update_layout(
        title="Activity Over Time",
        xaxis=dict(title="Timestamp"),
        yaxis=dict(title="Activity Metrics (Damage/Healing)", titlefont=dict(color="blue")),
        yaxis2=dict(
            title="Kills",
            titlefont=dict(color="red"),
            overlaying="y",
            side="right",
        ),
        legend=dict(x=0, y=1, bgcolor="rgba(255,255,255,0)", bordercolor="rgba(255,255,255,0)"),
        hovermode="x",
        template="plotly_white",
    )

    # Show the plot
    fig.show()


# Example usage
aggregated_fight_data = aggregate_fight_data(df, damage_threshold=500, kills_threshold=1)
plot_activity_plotly(aggregated_fight_data)


In [87]:
import pandas as pd

def sliding_window_analysis(df: pd.DataFrame, window_size: int = 10, damage_threshold: int = 500, kills_threshold: int = 1) -> pd.DataFrame:
    """
    Perform a sliding window analysis for fights.

    Parameters:
    - df: DataFrame with deltas calculated for cumulative metrics.
    - window_size: Size of the sliding window in seconds.
    - damage_threshold: Minimum total damage to consider a fight.
    - kills_threshold: Minimum total kills to consider a fight.

    Returns:
    - A DataFrame with sliding window aggregated metrics and fight indicators.
    """
    # Ensure timestamp is datetime
    df["timestamp"] = pd.to_datetime(df["timestamp"])

    # Sort by timestamp to ensure monotonic order
    df = df.sort_values(by="timestamp")

    # Set timestamp as index for rolling window calculation
    df = df.set_index("timestamp")

    # Fill missing values to avoid NaN propagation
    df = df.fillna(0)

    # Define rolling window (centered around each timestamp)
    rolling = df.rolling(f"{window_size}s", center=True)

    # Aggregate metrics within the sliding window
    aggregated = rolling[["damage_delta", "kills_delta", "healed_delta", "deaths_delta"]].sum()
    aggregated = aggregated.rename(columns={
        "damage_delta": "total_damage_window",
        "kills_delta": "total_kills_window",
        "healed_delta": "total_healed_window",
        "deaths_delta": "total_deaths_window"
    })

    # Reset index to merge back with the original DataFrame
    aggregated = aggregated.reset_index()

    # Flag timestamps as part of a fight based on thresholds
    aggregated["is_fight"] = (
        (aggregated["total_damage_window"] + aggregated["total_healed_window"] >= damage_threshold)
    )

    # Smooth fight detection: Require consecutive fights
    aggregated["is_fight"] = (
        aggregated["is_fight"].shift(1).fillna(False) &
        aggregated["is_fight"] &
        aggregated["is_fight"].shift(-1).fillna(False)
    )

    return aggregated


# Example usage
df = process_log_file("data/infoLog.txt")  # Parse and normalize data
df = calculate_deltas(df)  # Calculate deltas for cumulative metrics
sliding_window_fights = sliding_window_analysis(df, window_size=10, damage_threshold=500, kills_threshold=1)

# Save or analyze the sliding window fight data
sliding_window_fights.to_csv("sliding_window_fights.csv", index=False)
print(sliding_window_fights)


                            timestamp  total_damage_window  \
0    2024-11-28 19:08:54.152000+00:00                 0.00   
1    2024-11-28 19:09:01.175000+00:00                 0.00   
2    2024-11-28 19:10:40.136000+00:00                 0.00   
3    2024-11-28 19:11:37.715000+00:00                 0.00   
4    2024-11-28 19:16:07.813000+00:00              1089.46   
...                               ...                  ...   
8775 2024-11-28 20:53:59.571000+00:00              1019.65   
8776 2024-11-28 20:54:00.390000+00:00               793.07   
8777 2024-11-28 20:54:00.975000+00:00               793.07   
8778 2024-11-28 20:54:01.333000+00:00               793.07   
8779 2024-11-28 20:54:01.775000+00:00               514.45   

      total_kills_window  total_healed_window  total_deaths_window  is_fight  
0                    0.0               0.0000                  0.0     False  
1                    0.0               0.0000                  0.0     False  
2                 

C:\Users\dangy\AppData\Local\Temp\ipykernel_43136\1970878190.py:50: FutureWarning:

Downcasting object dtype arrays on .fillna, .ffill, .bfill is deprecated and will change in a future version. Call result.infer_objects(copy=False) instead. To opt-in to the future behavior, set `pd.set_option('future.no_silent_downcasting', True)`

C:\Users\dangy\AppData\Local\Temp\ipykernel_43136\1970878190.py:52: FutureWarning:

Downcasting object dtype arrays on .fillna, .ffill, .bfill is deprecated and will change in a future version. Call result.infer_objects(copy=False) instead. To opt-in to the future behavior, set `pd.set_option('future.no_silent_downcasting', True)`



In [88]:
import plotly.graph_objects as go

def plot_sliding_window_analysis(aggregated: pd.DataFrame):
    """
    Plot sliding window fight analysis using Plotly.

    Parameters:
    - aggregated: DataFrame with sliding window aggregated metrics and fight indicators.
    """
    # Convert timestamp to datetime if not already
    aggregated["timestamp"] = pd.to_datetime(aggregated["timestamp"])

    # Create a Plotly figure
    fig = go.Figure()

    # Add total damage to the primary y-axis
    fig.add_trace(
        go.Scatter(
            x=aggregated["timestamp"],
            y=aggregated["total_damage_window"],
            mode="lines",
            name="Total Damage",
            line=dict(width=2, color="blue"),
        )
    )

    # Add total healing to the primary y-axis
    fig.add_trace(
        go.Scatter(
            x=aggregated["timestamp"],
            y=aggregated["total_healed_window"],
            mode="lines",
            name="Total Healing",
            line=dict(width=2, color="green"),
        )
    )

    # Add total kills to the secondary y-axis
    fig.add_trace(
        go.Scatter(
            x=aggregated["timestamp"],
            y=aggregated["total_kills_window"],
            mode="lines",
            name="Total Kills",
            line=dict(width=2, color="red"),
            yaxis="y2",
        )
    )

    # Highlight fight periods with markers
    fight_timestamps = aggregated[aggregated["is_fight"]]["timestamp"]
    fig.add_trace(
        go.Scatter(
            x=fight_timestamps,
            y=[0] * len(fight_timestamps),
            mode="markers",
            name="Fight Periods",
            marker=dict(size=10, color="orange", symbol="circle"),
        )
    )

    # Update layout with dual y-axes
    fig.update_layout(
        title="Sliding Window Fight Analysis",
        xaxis=dict(title="Timestamp"),
        yaxis=dict(title="Activity Metrics (Damage/Healing)", titlefont=dict(color="blue")),
        yaxis2=dict(
            title="Kills",
            titlefont=dict(color="red"),
            overlaying="y",
            side="right",
        ),
        legend=dict(x=0, y=1, bgcolor="rgba(255,255,255,0)", bordercolor="rgba(255,255,255,0)"),
        hovermode="x",
        template="plotly_white",
    )

    # Show the plot
    fig.show()


# Example usage
sliding_window_fights = sliding_window_analysis(df, window_size=5, damage_threshold=500, kills_threshold=0)
plot_sliding_window_analysis(sliding_window_fights)


C:\Users\dangy\AppData\Local\Temp\ipykernel_43136\1970878190.py:50: FutureWarning:

Downcasting object dtype arrays on .fillna, .ffill, .bfill is deprecated and will change in a future version. Call result.infer_objects(copy=False) instead. To opt-in to the future behavior, set `pd.set_option('future.no_silent_downcasting', True)`

C:\Users\dangy\AppData\Local\Temp\ipykernel_43136\1970878190.py:52: FutureWarning:

Downcasting object dtype arrays on .fillna, .ffill, .bfill is deprecated and will change in a future version. Call result.infer_objects(copy=False) instead. To opt-in to the future behavior, set `pd.set_option('future.no_silent_downcasting', True)`



In [89]:
def identify_fight_ranges(df: pd.DataFrame) -> list:
    """
    Identify contiguous fight ranges (start and end timestamps).

    Parameters:
    - df: DataFrame with a boolean 'is_fight' column.

    Returns:
    - A list of dictionaries with fight start and end timestamps.
    """
    fights = []
    is_fight = df["is_fight"].values
    timestamps = df["timestamp"].values

    in_fight = False
    start_time = None

    for i, flag in enumerate(is_fight):
        if flag and not in_fight:
            # Fight starts
            in_fight = True
            start_time = timestamps[i]
        elif not flag and in_fight:
            # Fight ends
            in_fight = False
            fights.append({"start": start_time, "end": timestamps[i - 1]})

    # If a fight was still active at the end
    if in_fight:
        fights.append({"start": start_time, "end": timestamps[-1]})

    return fights
fight_ranges = identify_fight_ranges(sliding_window_fights)
print(fight_ranges)

[{'start': numpy.datetime64('2024-11-28T19:16:07.820000000'), 'end': numpy.datetime64('2024-11-28T19:16:22.851000000')}, {'start': numpy.datetime64('2024-11-28T19:16:30.355000000'), 'end': numpy.datetime64('2024-11-28T19:16:36.445000000')}, {'start': numpy.datetime64('2024-11-28T19:16:50.107000000'), 'end': numpy.datetime64('2024-11-28T19:17:17.820000000')}, {'start': numpy.datetime64('2024-11-28T19:17:24.892000000'), 'end': numpy.datetime64('2024-11-28T19:17:46.068000000')}, {'start': numpy.datetime64('2024-11-28T19:17:52.152000000'), 'end': numpy.datetime64('2024-11-28T19:18:33.861000000')}, {'start': numpy.datetime64('2024-11-28T19:18:45.233000000'), 'end': numpy.datetime64('2024-11-28T19:18:48.485000000')}, {'start': numpy.datetime64('2024-11-28T19:18:51.842000000'), 'end': numpy.datetime64('2024-11-28T19:19:10.105000000')}, {'start': numpy.datetime64('2024-11-28T19:19:17.248000000'), 'end': numpy.datetime64('2024-11-28T19:19:21.201000000')}, {'start': numpy.datetime64('2024-11-28T

In [90]:
from scipy.ndimage import gaussian_filter1d

def smooth_series_gaussian(series: pd.Series, sigma: float = 1.0) -> pd.Series:
    """
    Smooth a series using a Gaussian filter.

    Parameters:
    - series: The pandas Series to be smoothed.
    - sigma: The standard deviation for Gaussian kernel.

    Returns:
    - A smoothed pandas Series.
    """
    return pd.Series(gaussian_filter1d(series.values, sigma=sigma), index=series.index)


def plot_fight_ranges(df: pd.DataFrame, fight_ranges: list):
    """
    Plot sliding window metrics with fight ranges highlighted.

    Parameters:
    - df: DataFrame with sliding window metrics.
    - fight_ranges: List of dictionaries with fight start and end timestamps.
    """
    # Convert timestamp to datetime if not already
    df["timestamp"] = pd.to_datetime(df["timestamp"])

    # Ensure fight range timestamps are datetime
    for fight in fight_ranges:
        fight["start"] = pd.to_datetime(fight["start"])
        fight["end"] = pd.to_datetime(fight["end"])

    # Create a Plotly figure
    fig = go.Figure()

    # Add total damage to the primary y-axis
    fig.add_trace(
        go.Scatter(
            x=df["timestamp"],
            y=smooth_series_gaussian(df["total_damage_window"]),
            mode="lines",
            name="Total Damage",
            line=dict(width=2, color="blue"),
        )
    )

    # Add total healing to the primary y-axis
    fig.add_trace(
        go.Scatter(
            x=df["timestamp"],
            y=smooth_series_gaussian(df["total_healed_window"]),
            mode="lines",
            name="Total Healing",
            line=dict(width=2, color="green"),
        )
    )

    
    fig.add_trace(
        go.Scatter(
            x=df["timestamp"],
            y=smooth_series_gaussian(df["total_healed_window"] + df["total_damage_window"], sigma=2),
            mode="lines",
            name="Sum Healing Damage",
            line=dict(width=2, color="cyan"),
        )
    )

    # Add total kills to the secondary y-axis
    fig.add_trace(
        go.Scatter(
            x=df["timestamp"],
            y=smooth_series_gaussian(df["total_kills_window"]),
            mode="lines",
            name="Total Kills",
            line=dict(width=2, color="red"),
            yaxis="y2",
        )
    )

    # Highlight fight ranges using filled rectangles
    max_damage = df["total_damage_window"].max()
    for fight in fight_ranges:
        fig.add_trace(
            go.Scatter(
                x=[
                    fight["start"],
                    fight["end"],
                    fight["end"],
                    fight["start"],
                    fight["start"]
                ],
                y=[0, 0, max_damage, max_damage, 0],
                fill="toself",
                fillcolor="rgba(255,165,0,0.2)",  # Transparent orange
                line=dict(width=0),
                mode="lines",
                name="Fight Range",
                showlegend=False,
            )
        )

    # Update layout with dual y-axes
    fig.update_layout(
        title="Sliding Window Fight Analysis with Ranges",
        xaxis=dict(title="Timestamp"),
        yaxis=dict(title="Activity Metrics (Damage/Healing)", titlefont=dict(color="blue")),
        yaxis2=dict(
            title="Kills",
            titlefont=dict(color="red"),
            overlaying="y",
            side="right",
        ),
        legend=dict(x=0, y=1, bgcolor="rgba(255,255,255,0)", bordercolor="rgba(255,255,255,0)"),
        hovermode="x",
        template="plotly_white",
    )

    # Show the plot
    fig.show()


# Example usage
plot_fight_ranges(sliding_window_fights, fight_ranges)
